Try this Free online SD 1.5 generator with the results: https://perchance.org/fusion-ai-image-generator

 This Notebook is a Stable-diffusion tool which allows you to find similiar prompts to an existing prompt. It uses the Nearest Neighbor decoder method listed here:https://arxiv.org/pdf/2303.03032

THIS IS AN OLD VERSION OF THE CLIP INTERROGATOR.

YOU WILL FIND THE UP TO DATE VERSION HERE:https://huggingface.co/datasets/codeShare/fusion-t2i-generator-data/tree/main/Google%20Colab%20Jupyter%20Notebooks

In [ ]:
import os
home_directory = '/content/'
using_Kaggle = os.environ.get('KAGGLE_URL_BASE','')
if using_Kaggle : home_directory = '/kaggle/working/'
%cd {home_directory}

def fix_bad_symbols(txt):
  result = txt
  for symbol in ['^', '}', '{' , ')', '(', '[' , ']' , ':' , '=' ]:
    result = result.replace(symbol,'\\' + symbol)
  #------#
  return result;

def my_mkdirs(folder):
  if os.path.exists(folder)==False:
    os.makedirs(folder)

#🔸🔹
# Load the data if not already loaded
try:
    loaded
except:
  from safetensors.torch import load_file , save_file
  import json , torch , requests , math
  import pandas as pd
  from PIL import Image
  #----#
  %cd {home_directory}
  !git clone https://huggingface.co/datasets/codeShare/fusion-t2i-generator-data
  loaded = True
  %cd {home_directory + 'fusion-t2i-generator-data/'}
  !unzip vocab.zip
  !unzip reference.zip
#------#
%cd {home_directory + 'fusion-t2i-generator-data/' + 'vocab'}
with open(f'prompts.json', 'r') as f:
  data = json.load(f)
  _df = pd.DataFrame({'count': data})['count']
  prompts = {
      key : value for key, value in _df.items()
  }
#-------#
%cd {home_directory + 'fusion-t2i-generator-data/' + 'reference'}
with open(f'reference_prompts.json', 'r') as f:
  data = json.load(f)
  _df = pd.DataFrame({'count': data})['count']
  target_prompts = {
      key : value for key, value in _df.items()
  }
#------#
with open(f'reference_urls.json', 'r') as f:
  data = json.load(f)
  _df = pd.DataFrame({'count': data})['count']
  target_urls = {
      key : value for key, value in _df.items()
  }
from transformers import AutoTokenizer
tokenizer = AutoTokenizer.from_pretrained("openai/clip-vit-large-patch14", clean_up_tokenization_spaces = False)
from transformers import  CLIPProcessor, CLIPModel
processor = CLIPProcessor.from_pretrained("openai/clip-vit-large-patch14" , clean_up_tokenization_spaces = True)
model = CLIPModel.from_pretrained("openai/clip-vit-large-patch14")
logit_scale = model.logit_scale.exp() #logit_scale = 100.00000762939453

index = 0
%cd {home_directory + 'fusion-t2i-generator-data/' + 'vocab'}
vocab_encodings = torch.load('vocab_encodings.pt', weights_only=False)
for key in vocab_encodings:
  index = index + 1;
#------#
NUM_VOCAB_ITEMS = index

index = 0
%cd {home_directory + 'fusion-t2i-generator-data/' + 'reference'}
for key in torch.load('reference_text_and_image_encodings.pt', weights_only=False):
  index = index + 1;
#------#
NUM_REFERENCE_ITEMS = index



In [ ]:
# @title 	⚄ Use a pre-encoded prompt + image pair from the fusion gen (note: NSFW!)
# @markdown Choose a pre-encoded reference
index = 213 # @param {type:"slider", min:0, max:1666, step:1}
PROMPT_INDEX = index
prompt = target_prompts[f'{PROMPT_INDEX}']
url = target_urls[f'{PROMPT_INDEX}']
if url.find('perchance')>-1:
  image = Image.open(requests.get(url, stream=True).raw)
#------#
# @markdown ⚖️ 🖼️ encoding <-----?-----> 📝 encoding </div> <br>
C = 0.3 # @param {type:"slider", min:0, max:1, step:0.01}
log_strength_1 = 2.17 # @param {type:"slider", min:-5, max:5, step:0.01}
prompt_strength = torch.tensor(math.pow(10 ,log_strength_1-1)).to(dtype = torch.float32)
reference = torch.zeros(768).to(dtype = torch.float32)

%cd {home_directory + 'fusion-t2i-generator-data/' + 'reference'}
references = torch.load('reference_text_and_image_encodings.pt'  , weights_only=False)
reference = torch.add(reference, prompt_strength * C * references[index][0].dequantize().to(dtype = torch.float32))
reference = torch.add(reference, prompt_strength * (1-C) * references[index][1].dequantize().to(dtype = torch.float32))
references = '' # Clear up memory
# @markdown -----------
# @markdown 📝➕ 1st Enhance similarity to prompt(s)
POS_2 = '' # @param {type:'string' ,placeholder:'item1 , item2 , ...'}
log_strength_2 = 1.03 # @param {type:"slider", min:-5, max:5, step:0.01}
pos_strength = torch.tensor(math.pow(10 ,log_strength_2-1)).to(dtype = torch.float32)
for _POS in POS_2.replace('</w>' , ' ').replace('{' , '').replace('}' , '').replace('|' , ',').split(','):
  inputs = tokenizer(text = _POS.strip(), truncation = True  , padding=True, return_tensors="pt")
  text_features_POS = model.get_text_features(**inputs).to(dtype = torch.float32)
  text_features_POS = text_features_POS/text_features_POS.norm(p=2, dim=-1, keepdim=True)
  reference = torch.add(reference, pos_strength * text_features_POS)
# @markdown -----------

# @markdown -----------
# @markdown 📝➕ 2nd Enhance similarity to prompt(s)
POS = '' # @param {type:'string' ,placeholder:'item1 , item2 , ...'}
log_strength_3 = 1.06 # @param {type:"slider", min:-5, max:5, step:0.01}
pos_strength = torch.tensor(math.pow(10 ,log_strength_3-1)).to(dtype = torch.float32)
for _POS in POS.replace('</w>' , ' ').replace('{' , '').replace('}' , '').replace('|' , ',').split(','):
  inputs = tokenizer(text = _POS.strip(), truncation = True  , padding=True, return_tensors="pt")
  text_features_POS = model.get_text_features(**inputs).to(dtype = torch.float32)
  text_features_POS = text_features_POS/text_features_POS.norm(p=2, dim=-1, keepdim=True)
  reference = torch.add(reference, pos_strength * text_features_POS)
# @markdown -----------

# @markdown 🚫 Penalize similarity to prompt(s)
NEG = '' # @param {type:'string' , placeholder:'item1 , item2 , ...'}
log_strength_4 = 1 # @param {type:"slider", min:-5, max:5, step:0.01}
neg_strength = torch.tensor(math.pow(10 ,log_strength_4-1)).to(dtype = torch.float32)
for _NEG in NEG.replace('</w>' , ' ').replace('{' , '').replace('}' , '').replace('|' , ',').split(','):
  inputs = tokenizer(text = _NEG.strip(), truncation = True  , padding=True, return_tensors="pt")
  text_features_NEG = model.get_text_features(**inputs).to(dtype = torch.float32)
  text_features_NEG = text_features_NEG/text_features_NEG.norm(p=2, dim=-1, keepdim=True)
  reference = torch.sub(reference, neg_strength * text_features_NEG)
# @markdown -----------
# @markdown ⏩ Skip item(s) containing the word(s)
SKIP = '' # @param {type:'string' , placeholder:'item1 , item2 , ...'}

min_wordcount = 0 # @param {type:"slider", min:0, max:20, step:1}

def isBlacklisted(_txt, _blacklist):
  blacklist =  _blacklist.lower().replace('</w>' , ' ').replace('{' , '').replace('}' , '').replace('|' , ',').strip()
  txt = _txt.lower().strip()
  if len(txt)<min_wordcount: return True
  if txt.isnumeric(): return True
  if blacklist == '': return False
  for item in list(blacklist.split(',')):
    if item.strip() == '' : continue
    if txt.find(item.strip())> -1 : return True
  #------#
  found = False
  alphabet = 'abcdefghijklmnopqrstuvxyz'
  for letter in alphabet:
    found =  txt.find(letter)>-1
    if found:break
  #------#
  return not found

# @markdown -----------
# @markdown 🔍 How similar should the results be?
list_size = 1000 # @param {type:'number'}
start_at_index = 1 # @param {type:'number'}
# @markdown -----------
# @markdown Repeat output N times
N = 7 # @param {type:"slider", min:0, max:20, step:1}
# @markdown -----------
# @markdown ⚙️ Run the script?
update_list = True # @param {type:"boolean"}

calculate_variance  = False # @param {type:"boolean"}

ne = update_list

try: first
except:
  enable = True
  first = True

if (enable):
  reference = reference/reference.norm(p=2, dim=-1, keepdim=True)
  %cd {home_directory + 'fusion-t2i-generator-data/' + 'vocab'}
  sims = torch.matmul(vocab_encodings.dequantize(),reference.t())
  sorted , indices = torch.sort(sims,dim=0 , descending=True)

  if calculate_variance:
    average = torch.zeros(768)
    for key in range(NUM_VOCAB_ITEMS):
      if (key>=start_at_index and key < start_at_index + list_size):
        average = torch.add(average, vocab_encodings[key].dequantize())
      if (key>=start_at_index + list_size) : break
    average = average * (1/max(1, list_size))
    average = average/average.norm(p=2, dim=-1, keepdim=True)
    average = average.clone().detach();
    variance = torch.zeros(1)
    for key in range(NUM_VOCAB_ITEMS):
      if (key>=start_at_index and key < start_at_index + list_size):
        #dot product
        difference_to_average = 100 * (torch.ones(1) - torch.dot(average[0]
        , vocab_encodings[key].dequantize()[0])/average.norm(p=2, dim=-1, keepdim=True))
        variance =  torch.add(variance, difference_to_average * difference_to_average)
      if (key>=start_at_index + list_size) : break
    #--------#
    variance =  variance * (1/max(1, list_size))
    variance= variance.clone().detach();
    print(f'The variance for the selected range is {math.sqrt(variance.item())} units from average')
  #--------#
#---#
output = '{'
for _index in range(list_size):
  tmp = prompts[f'{indices[min(_index+start_at_index,NUM_VOCAB_ITEMS-1)].item()}']
  if isBlacklisted(tmp , SKIP): continue
  tmp = fix_bad_symbols(tmp)
  if output.find(tmp)>-1:continue
  output = output + tmp + '|'
#---------#
output = (output + '}').replace('|}' , '} ')
print('')
print('')
for iter in range(N):
  print(output)
#-------#
print('')
print('')
image or print('No image found')

In [ ]:
# Check the average value for this set
sims = torch.matmul(vocab_encodings.dequantize(),average.t())
sorted , indices = torch.sort(sims,dim=0 , descending=True)
for index in range(10):
  print(prompts[f'{indices[index].item()}'])

In [ ]:
# @title ⚙️📝 Print the results (Advanced)
list_size = 1000 # @param {type:'number'}
start_at_index = 0 # @param {type:'number'}
print_Similarity = True # @param {type:"boolean"}
print_Prompts = True # @param {type:"boolean"}
print_Descriptions = True # @param {type:"boolean"}
compact_Output = True # @param {type:"boolean"}
newline_Separator = False # @param {type:"boolean"}

import random
# @markdown -----------
# @markdown Mix with...
list_size2 = 1000 # @param {type:'number'}
start_at_index2 = 10000 # @param {type:'number'}
rate_percent  = 0 # @param {type:"slider", min:0, max:100, step:1}

# @markdown -----------
# @markdown Repeat output N times
N = 6 # @param {type:"slider", min:0, max:10, step:1}

# title Show the 100 most similiar suffix and prefix text-encodings to the text encoding
RANGE = list_size
separator = '|'
if newline_Separator : separator = separator + '\n'

_prompts = ''
_sims =  ''
for _index in range(start_at_index + RANGE):
  if _index < start_at_index : continue
  index = indices[_index].item()

  prompt = prompts[f'{index}']
  if rate_percent >= random.randint(0,100) : prompt = prompts[f'{random.randint(start_at_index2 , start_at_index2 + list_size2)}']

  #Remove duplicates
  if _prompts.find(prompt + separator)<=-1:
    _sims = _sims + f'{round(100*sims[index].item(), 2)} %' + separator
  #-------#
  _prompts = _prompts.replace(prompt + separator,'')
  _prompts = _prompts  + prompt + separator
  #------#
#------#
__prompts = fix_bad_symbols(__prompts)
__prompts = ('{' + _prompts + '}').replace(separator + '}', '}')
__sims = ('{' + _sims + '}').replace(separator + '}', '}')
#------#

if(not print_Prompts): __prompts = ''
if(not print_Similarity): __sims = ''

if(not compact_Output):
  if(print_Descriptions):
    print(f'The {start_at_index}-{start_at_index + RANGE} most similiar items to prompt : \n\n ')
    for i in range(N) : print(__prompts)
    print(f'The {start_at_index}-{start_at_index + RANGE} similarity % for items : \n\n' + __sims)
    print('')
  else:
    for i in range(N) : print(__prompts)
else:
  for i in range(N) : print(__prompts)
#-------#

The savefile can be used here : https://perchance.org/fusion-ai-image-generator

In [ ]:
# @title 	⚄ Create fusion-generator .json savefile from result
filename = 'blank.json'
path = '/content/text-to-image-prompts/fusion/'

print(f'reading {filename}....')
_index = 0
%cd {path}
with open(f'{filename}', 'r') as f:
  data = json.load(f)
#------#
_df = pd.DataFrame({'count': data})['count']
_savefile = {
    key : value for key, value in _df.items()
}
#------#
from safetensors.torch import load_file
import json , os , torch
import pandas as pd
#----#
def my_mkdirs(folder):
  if os.path.exists(folder)==False:
    os.makedirs(folder)
#------#
savefile_prompt = ''
for i in range(N) : savefile_prompt = savefile_prompt + ' ' + __prompts
_savefile['main'] = savefile_prompt.replace('\n', ' ').replace('  ', ' ').replace('   ', ' ')
#------#
save_filename = f'fusion_C05_X7_1000_{PROMPT_INDEX}.json'
output_folder = '/content/output/savefiles/'
my_mkdirs(output_folder)
#-----#
%cd {output_folder}
print(f'Saving segment {save_filename} to {output_folder}...')
with open(save_filename, 'w') as f:
    json.dump(_savefile, f)


In [ ]:
# @title 	⚄ Create a savefile-set from the entire range of pre-encoded items

# @markdown 📥 Load the data (only required one time)
load_the_data = True # @param {type:"boolean"}

import math
from safetensors.torch import load_file
import json , os , torch
import pandas as pd
from PIL import Image
import requests

def my_mkdirs(folder):
  if os.path.exists(folder)==False:
    os.makedirs(folder)

# @markdown ⚖️ Set the value for C in the reference  <br> <br> sim = C* text_enc + image_enc*(1-C) <br><br>

C = 0.5 # @param {type:"slider", min:0, max:1, step:0.01}

# @markdown 🚫 Penalize similarity to this prompt(optional)
if(load_the_data):
  target_prompts , target_text_encodings , urls , target_image_encodings , NUM_ITEMS =  getPromptsAndLinks('/content/text-to-image-prompts/fusion')
  from transformers import AutoTokenizer
  tokenizer = AutoTokenizer.from_pretrained("openai/clip-vit-large-patch14", clean_up_tokenization_spaces = False)
  from transformers import  CLIPProcessor, CLIPModel
  processor = CLIPProcessor.from_pretrained("openai/clip-vit-large-patch14" , clean_up_tokenization_spaces = True)
  model = CLIPModel.from_pretrained("openai/clip-vit-large-patch14")
  logit_scale = model.logit_scale.exp() #logit_scale = 100.00000762939453
#---------#

filename = 'blank.json'
path = '/content/text-to-image-prompts/fusion/'
print(f'reading {filename}....')
_index = 0
%cd {path}
with open(f'{filename}', 'r') as f:
  data = json.load(f)
#------#
_df = pd.DataFrame({'count': data})['count']
_blank = {
    key : value for key, value in _df.items()
}
#------#

root_savefile_name = 'fusion_C05_X7'

%cd /content/
output_folder = '/content/output/savefiles/'
my_mkdirs(output_folder)
my_mkdirs('/content/output2/savefiles/')
my_mkdirs('/content/output3/savefiles/')
my_mkdirs('/content/output4/savefiles/')
my_mkdirs('/content/output5/savefiles/')
my_mkdirs('/content/output6/savefiles/')
my_mkdirs('/content/output7/savefiles/')
my_mkdirs('/content/output8/savefiles/')
my_mkdirs('/content/output9/savefiles/')
my_mkdirs('/content/output10/savefiles/')
my_mkdirs('/content/output11/savefiles/')
my_mkdirs('/content/output12/savefiles/')
my_mkdirs('/content/output13/savefiles/')


NEG = '' # @param {type:'string'}
strength = 1 # @param {type:"slider", min:-5, max:5, step:0.1}

for index in range(1667):

  PROMPT_INDEX = index
  prompt = target_prompts[f'{index}']
  url = urls[f'{index}']
  if url.find('perchance')>-1:
    image = Image.open(requests.get(url, stream=True).raw)
  else: continue #print("(No image for this ID)")

  print(f"no. {PROMPT_INDEX} : '{prompt}'")
  text_features_A = target_text_encodings[f'{index}']
  image_features_A =  target_image_encodings[f'{index}']
  # text-similarity
  sims =  C * torch.matmul(text_tensor, text_features_A.t())

  neg_sims = 0*sims
  if(NEG != ''):
    # Get text features for user input
    inputs = tokenizer(text = NEG, padding=True, return_tensors="pt")
    text_features_NEG = model.get_text_features(**inputs)
    text_features_NEG = text_features_A/text_features_A.norm(p=2, dim=-1, keepdim=True)
    # text-similarity
    neg_sims =  strength*torch.matmul(text_tensor, text_features_NEG.t())
  #------#

  # plus image-similarity
  sims = sims +  (1-C) * torch.matmul(text_tensor, image_features_A.t()) * logit_scale

  # minus NEG-similarity
  sims = sims - neg_sims

  # Sort the items
  sorted , indices = torch.sort(sims,dim=0 , descending=True)

  # @markdown Repeat output N times
  RANGE = 1000
  NUM_CHUNKS = 10+
  separator = '|'
  _savefiles = {}
  #-----#
  for chunk in range(NUM_CHUNKS):
    if chunk=<10:continue
    start_at_index = chunk * RANGE
    _prompts = ''
    for _index in range(start_at_index + RANGE):
      if _index < start_at_index : continue
      index = indices[_index].item()
      prompt = prompts[f'{index}']
      _prompts = _prompts.replace(prompt + separator,'')
      _prompts = _prompts  + prompt + separator
    #------#
    _prompts = fix_bad_symbols(_prompts)
    _prompts = ('{' + _prompts + '}').replace(separator + '}', '}')
    _savefiles[f'{chunk}'] = _prompts
  #---------#
  save_filename = f'{root_savefile_name}_{start_at_index + RANGE}_{PROMPT_INDEX}.json'


  if (chunk=<20 && chunk>10): %cd '/content/output2/savefiles/'
  if (chunk<=30 && chunk>20): %cd '/content/output3/savefiles/'
  if (chunk=<40 && chunk>30): %cd '/content/output4/savefiles/'
  if (chunk<=50 && chunk>40): %cd '/content/output5/savefiles/'
  if (chunk=<60 && chunk>50): %cd '/content/output6/savefiles/'
  if (chunk<=70 && chunk>60): %cd '/content/output7/savefiles/'
  if (chunk=<80 && chunk>70): %cd '/content/output8/savefiles/'
  if (chunk<=90 && chunk>80): %cd '/content/output9/savefiles/'
  if (chunk=<100 && chunk>90): %cd '/content/output10/savefiles/'
  if (chunk<=110 && chunk>100): %cd '/content/output11/savefiles/'
  if (chunk=<120 && chunk>110): %cd '/content/output12/savefiles/'
  if (chunk<=130 && chunk>120): %cd '/content/output13/savefiles/'


  #------#
  print(f'Saving savefile {save_filename} to {output_folder}...')
  with open(save_filename, 'w') as f:
      json.dump(_savefiles, f)
  #---------#
  continue
#-----------#

In [ ]:
# Determine if this notebook is running on Colab or Kaggle
#Use https://www.kaggle.com/ if Google Colab GPU is busy
home_directory = '/content/'
using_Kaggle = os.environ.get('KAGGLE_URL_BASE','')
if using_Kaggle : home_directory = '/kaggle/working/'
%cd {home_directory}
#-------#

# @title Download the text_encodings as .zip
import os
%cd {home_directory}
#os.remove(f'{home_directory}results.zip')
root_output_folder = home_directory + 'output/'
zip_dest = f'/content/results.zip' #drive/MyDrive
!zip -r {zip_dest} {root_output_folder}

In [ ]:
# @title 	⚄ New code (work in progress)

def get_num_vocab_items(_url):
  num_vocab_items = 0
  for item in _url.split('_'):
    if item.find('safetensors')>-1: num_vocab_items = int(item.replace('.safetensors', ''))
  #------#
  return num_vocab_items-1


def get_similiar(_ref , urls, _LIST_SIZE):
  dot_dtype = torch.float16
  _SCALE = torch.tensor(0.0043).to(dot_dtype)
  _DIM = 768
  _vocab = {}
  #----#
  inputs = tokenizer(text = _ref.strip(), truncation = True  , padding=True, return_tensors="pt")
  ref = model.get_text_features(**inputs)[0]
  ref = (ref/ref.norm(p=2, dim=-1, keepdim=True)).to(dtype = dot_dtype)
  #-----#
  num_vocab_items = 0
  for url in urls:
    num_vocab_items = num_vocab_items + get_num_vocab_items(url)
  #------#
  vocab = torch.zeros(num_vocab_items , _DIM).to(torch.uint8)
  prompts = {}
  index = 0
  for url in urls:
    __vocab = load_file(url)
    for key in load_file(url):
      vocab[index] = __vocab[key][1:_DIM+1] - __vocab[key][0]*torch.ones(_DIM).t()
      prompts[f'{index}'] = key
      index = index + 1
    #-------#
    __vocab = {}
  #-------#
  sims = torch.matmul((vocab*_SCALE).to(dot_dtype) , ref.t())
  sorted , indices = torch.sort(sims, dim = 0 , descending = True)
  return indices , prompts , sims
  _prompts = {}
  for index in range(num_vocab_items):
    key = prompts[f'{indices[index]}']
    _prompts[f'{key}'] = sims[key].item()
    index = index + 1
    if index>_LIST_SIZE:break
  #-------#
  return _prompts
#-------#



In [ ]:
vocab = {}
# @title 	⚄ New code (work in progress)
ref = 'impressionist painting by luis royo' # @param {type:'string' , placeholder:'type a single prompt to match'}
LIST_SIZE = 1000  # @param {type:'number' , placeholder:'set how large the list should be'}
urls = [ '/content/fusion-t2i-generator-data/civitai_vocab_q0043_203663.safetensors' ,]

         #'/content/fusion-t2i-generator-data/clip_vocab_q0043_541291.safetensors' , '/content/fusion-t2i-generator-data/lyrics_vocab_q0043_41905.safetensors' , '/content/fusion-t2i-generator-data/names_vocab_q0043_162977.safetensors' , '/content/fusion-t2i-generator-data/r34_vocab_q0043_96166.safetensors' ]

indices , prompts , sims = get_similiar(ref , urls , LIST_SIZE)

index = 0
_prompts = {}
for index in range(203662):
  try:
    key = prompts[f'{indices[index].item()}']
    print(key)
  except: print('Not found!')
  #_prompts[f'{key}'] = sims[key].item()
  index = index + 1
  if index>LIST_SIZE:break

